In [2]:
import tensorflow as tf
import numpy as np
from tensorflow.keras.utils import get_custom_objects
from PIL import Image

def leaky_relu_activation(x):
    return tf.nn.leaky_relu(x, alpha=0.1)

class SinglePixelAttention(tf.keras.layers.Layer):
    def __init__(self, **kwargs):
        super(SinglePixelAttention, self).__init__(**kwargs)
        
    def call(self, inputs):
        mean_values = tf.reduce_mean(inputs, axis=-1)
        max_indices = tf.argmax(mean_values, axis=-1)
        attention_mask = tf.one_hot(max_indices, depth=tf.shape(inputs)[1])
        attention_mask = tf.expand_dims(attention_mask, axis=-1)
        attention_output = inputs * attention_mask
        return attention_output

class DepthToSpace(tf.keras.layers.Layer):
    def __init__(self, scale, **kwargs):
        super(DepthToSpace, self).__init__(**kwargs)
        self.scale = scale
        
    def call(self, inputs):
        return tf.nn.depth_to_space(inputs, self.scale)

class CustomDepthwiseConv2D(tf.keras.layers.DepthwiseConv2D):
    def __init__(self, **kwargs):
        if 'groups' in kwargs:
            del kwargs['groups']
        super(CustomDepthwiseConv2D, self).__init__(**kwargs)

get_custom_objects().update({
    'leaky_relu_activation': leaky_relu_activation,
    'SinglePixelAttention': SinglePixelAttention,
    'DepthToSpace': DepthToSpace,
    'mse': tf.keras.losses.MeanSquaredError(),
    'DepthwiseConv2D': CustomDepthwiseConv2D
})

def load_model(model_path):
    try:
        model = tf.keras.models.load_model(model_path, compile=False)
        print(f"Successfully loaded model from {model_path}")
        return model
    except Exception as e:
        print(f"Error loading model {model_path}: {e}")
        return None

binary_classifier = load_model('mob_clssifc.h5')
espcn_model = load_model('espcn_model.h5')

if binary_classifier is not None and espcn_model is not None:
    print("Both models loaded successfully")
else:
    print("Failed to load one or both models")

Successfully loaded model from mob_clssifc.h5

Successfully loaded model from espcn_model.h5
Both models loaded successfully


In [3]:
patch_size = 10
stride = int(patch_size/2)
scale_size = 6

In [4]:
#Create patches of the pixelated image
def extract_patches(image, patch_size=10, stride=5):
    patches = []
    indices = []
    for i in range(0, image.shape[0] - patch_size + 1, stride):
        for j in range(0, image.shape[1] - patch_size + 1, stride):
            patch = image[i:i+patch_size, j:j+patch_size, :]
            patches.append(patch)
            indices.append((i, j))
    return np.array(patches), indices

In [5]:
#Reconstruct the image after processing
def reconstruct_image(patches, indices, image_shape, patch_size=10, stride=5, scale_factor=6):
    h, w, c = image_shape
    output_shape = (h * scale_factor, w * scale_factor, c)
    output_image = np.zeros(output_shape, dtype=np.float32)
    weight_sum = np.zeros(output_shape, dtype=np.float32)
    patch_size_scaled = patch_size * scale_factor

    for patch, (i, j) in zip(patches, indices):
        scaled_patch = espcn_model.predict(np.expand_dims(patch, axis=0))[0]
        i_scaled, j_scaled = i * scale_factor, j * scale_factor
        y, x = np.ogrid[-patch_size_scaled//2:patch_size_scaled//2, -patch_size_scaled//2:patch_size_scaled//2]
        weight = np.exp(-(x*x + y*y) / (2 * (patch_size_scaled/4)**2))
        weight = weight[:,:,np.newaxis]
        weight = np.repeat(weight, c, axis=2)
        output_image[i_scaled:i_scaled+patch_size_scaled, j_scaled:j_scaled+patch_size_scaled] += scaled_patch * weight
        weight_sum[i_scaled:i_scaled+patch_size_scaled, j_scaled:j_scaled+patch_size_scaled] += weight

    mask = weight_sum != 0
    output_image[mask] /= weight_sum[mask]
    crop_size = 5 * scale_factor
    output_image = output_image[crop_size:-crop_size, crop_size:-crop_size]
    output_image_resized = tf.image.resize(output_image, [h, w], method=tf.image.ResizeMethod.BICUBIC).numpy()
    
    return output_image_resized

In [6]:
#Convert RGB to YUV and YUV to RGB
def rgb_to_yuv(rgb_image):
    rgb_image = rgb_image.astype(np.float32) / 255.0
    
    conversion_matrix = np.array([
        [0.299, 0.587, 0.114],
        [-0.14713, -0.28886, 0.436],
        [0.615, -0.51499, -0.10001]
    ])
    
    yuv_image = np.dot(rgb_image, conversion_matrix.T)
    yuv_image[:,:,1:] += 0.5
    return yuv_image

def yuv_to_rgb(yuv_image):
    yuv_image = yuv_image.astype(np.float32)
    yuv_image[:,:,1:] -= 0.5
    
    conversion_matrix = np.array([
        [1, 0, 1.13983],
        [1, -0.39465, -0.58060],
        [1, 2.03211, 0]
    ])
    
    rgb_image = np.dot(yuv_image, conversion_matrix.T)
    rgb_image = np.clip(rgb_image, 0, 1) * 255
    return rgb_image.astype(np.uint8)


In [8]:
#Process the image if pixelation is found
def process_image(image_path):
    input_image = Image.open(image_path)
    input_image = tf.keras.preprocessing.image.img_to_array(input_image)
    input_image_yuv = rgb_to_yuv(input_image)
    patches, indices = extract_patches(input_image_yuv, patch_size=10, stride=5)
    output_image_yuv = reconstruct_image(patches, indices, input_image_yuv.shape, patch_size=10, stride=5, scale_factor=6)
    output_image_rgb = yuv_to_rgb(output_image_yuv)
    output_image = Image.fromarray(output_image_rgb.astype('uint8'))
    return output_image

In [9]:
#Classification verdict from binary_classifier
def classifier_verdict(binary_classifier, image_path):
    img = Image.open(image_path)
    img = np.array(img)
    img = tf.convert_to_tensor(img, dtype=tf.float32) / 255.0
    temp_img = tf.image.resize(img, (224, 224))
    prediction = binary_classifier.predict(tf.expand_dims(temp_img, 0))[0]
    return prediction

In [12]:
if __name__ == "__main__":
    input_image_path = "temp5_low.jpg"
    
    prediction = classifier_verdict(binary_classifier, input_image_path)
    if prediction > 0.9:
        print("Image classified as non-pixelated. Returning original image.")
    else:
        print("Image classified as pixelated. Processing with ESPCN.")
        output_image = process_image(input_image_path)
        output_image.save('output.jpg')
        im = Image.open('output.jpg')
        im.show()
        print("Processing complete. Output saved as 'output.jpg'")

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 919ms/step
Image classified as pixelated. Processing with ESPCN.
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 58ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/